In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load
# 5cfcb5e8ef8458be6e85d57c45c7573477e2ad6a

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import warnings
warnings.filterwarnings("ignore")

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
df = pd.read_csv("/kaggle/input/2025-sep-dl-gen-ai-project/train.csv") #training set
dt = pd.read_csv("/kaggle/input/2025-sep-dl-gen-ai-project/test.csv")  #test set

In [3]:
from sklearn.model_selection import train_test_split

label_cols = ['anger','fear','joy','sadness','surprise']

xtrain, xval, ytrain, yval = train_test_split(
    df['text'],
    df[label_cols].values,
    test_size=0.2,
    random_state=42,
    shuffle=True
)

In [4]:
# from kaggle_secrets import UserSecretsClient
# user_secrets = UserSecretsClient()
# wdb_t = user_secrets.get_secret("WB_TOKEN")
# import wandb
# wandb.login(key=wdb_t)
# # wandb.init(project="22f3001086-t32025", name = "BERT+Classifier head")

wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: vaishnavib (vaishnavib-iitm-jntuh-) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [5]:
# !pip install nlpaug

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.5/410.5 kB 13.5 MB/s eta 0:00:00


In [7]:
# # --- SETUP AND IMPORTS ---
# import torch
# import torch.nn as nn
# from torch.utils.data import Dataset, DataLoader
# from sklearn.metrics import f1_score
# from transformers import AutoTokenizer, AutoModel, get_linear_schedule_with_warmup
# from torch.optim import AdamW
# from tqdm.auto import tqdm
# import nlpaug.augmenter.word as naw
# import wandb

# DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
# print(f"Using device: {DEVICE}")

# CONFIG = {
#     'MODEL_NAME': 'microsoft/deberta-v3-base',   # DeBERTa
#     'LEARNING_RATE': 2e-5,
#     'BATCH_SIZE': 32,
#     'EPOCHS': 6,
#     'MAX_LEN': 128,
#     'RANDOM_SEED': 42,
#     'DROPOUT': 0.1,
#     'WEIGHT_DECAY': 0.01,
#     'WARMUP_RATIO': 0.1,
#     'OUTPUT_DIM': 5
# }

# torch.manual_seed(CONFIG['RANDOM_SEED'])
# np.random.seed(CONFIG['RANDOM_SEED'])

# # --- NLP AUGMENTER (same as RoBERTa) ---
# import nltk
# nltk.download('averaged_perceptron_tagger_eng')
# syn_aug = naw.SynonymAug(aug_max=1, stopwords=['i', 'am', 'the', 'a', 'to', 'is'])

# def augment_sample(row, aug_count=1):
#     new_rows = []
#     text = row['text']
#     for _ in range(aug_count):
#         aug_text = syn_aug.augment(text)[0]
#         new_row = row.copy()
#         new_row['text'] = aug_text
#         new_rows.append(new_row)
#     return pd.DataFrame(new_rows)

# # Build full train/val dataframes
# df_full = df.copy()
# df_train, df_val = train_test_split(
#     df_full,
#     test_size=0.2,
#     random_state=CONFIG['RANDOM_SEED'],
#     shuffle=True
# )

# print(f"Initial Training Samples: {len(df_train)}")

# # --- TARGETED AUGMENTATION FOR ANGER & JOY ---
# anger_samples = df_train[df_train['anger'] == 1]
# joy_samples   = df_train[df_train['joy'] == 1]

# print(f"Initial Anger Samples: {len(anger_samples)}")
# print(f"Initial Joy Samples: {len(joy_samples)}")

# augmented_parts = []

# # anger: 2x augmentation
# for _, row in anger_samples.iterrows():
#     augmented_parts.append(augment_sample(row, aug_count=2))

# # joy: 1x augmentation
# for _, row in joy_samples.iterrows():
#     augmented_parts.append(augment_sample(row, aug_count=1))

# if augmented_parts:
#     df_aug = pd.concat(augmented_parts, ignore_index=True)
#     df_train_aug = pd.concat([df_train, df_aug], ignore_index=True)
# else:
#     df_train_aug = df_train.copy()

# print(f"Training samples after augmentation: {len(df_train_aug)}")

# # --- POSITIVE CLASS WEIGHTS FOR BCE ---
# CLASS_COUNTS = {
#     'anger': 808,
#     'fear': 3860,
#     'joy': 1660,
#     'sadness': 2171,
#     'surprise': 1999
# }

# N_TRAIN = len(df_train_aug)
# pos_weight_list = []
# for label in label_cols:
#     total_count_i = CLASS_COUNTS[label]
#     count_i = max(1, int(total_count_i * 0.8))  # same heuristic as RoBERTa script
#     weight = (N_TRAIN - count_i) / count_i
#     pos_weight_list.append(weight)

# POS_WEIGHTS = torch.tensor(pos_weight_list, dtype=torch.float).to(DEVICE)
# print("pos_weights:", POS_WEIGHTS.tolist())

Using device: cuda
Initial Training Samples: 5461
Initial Anger Samples: 647
Initial Joy Samples: 1339


[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /usr/share/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


Training samples after augmentation: 8094
pos_weights: [11.529411315917969, 1.6211140155792236, 5.094879627227783, 3.662442445755005, 4.06191349029541]


Training samples after augmentation: 8094
pos_weights: [11.529411315917969, 1.6211140155792236, 5.094879627227783, 3.662442445755005, 4.06191349029541]

In [9]:
# # --- DATASET ---
# class EmotionDataset(Dataset):
#     def __init__(self, df, tokenizer, max_len):
#         self.texts = df['text'].values
#         self.labels = df[label_cols].values
#         self.tokenizer = tokenizer
#         self.max_len = max_len

#     def __len__(self):
#         return len(self.texts)

#     def __getitem__(self, index):
#         text = str(self.texts[index])
#         labels = self.labels[index]

#         enc = self.tokenizer.encode_plus(
#             text,
#             add_special_tokens=True,
#             max_length=self.max_len,
#             padding='max_length',
#             truncation=True,
#             return_attention_mask=True,
#             return_tensors='pt',
#         )

#         return {
#             'input_ids': enc['input_ids'].flatten(),
#             'attention_mask': enc['attention_mask'].flatten(),
#             'labels': torch.tensor(labels, dtype=torch.float)
#         }

# tokenizer = AutoTokenizer.from_pretrained(CONFIG['MODEL_NAME'])

# train_ds = EmotionDataset(df_train_aug, tokenizer, CONFIG['MAX_LEN'])
# val_ds   = EmotionDataset(df_val,       tokenizer, CONFIG['MAX_LEN'])

# train_loader = DataLoader(train_ds, batch_size=CONFIG['BATCH_SIZE'], shuffle=True,  num_workers=2)
# val_loader   = DataLoader(val_ds,   batch_size=CONFIG['BATCH_SIZE'], shuffle=False, num_workers=2)

# # --- DEBERTA CLASSIFIER ---
# class DebertaClassifier(nn.Module):
#     def __init__(self, n_classes, model_name, dropout):
#         super(DebertaClassifier, self).__init__()
#         self.backbone = AutoModel.from_pretrained(model_name)
#         self.drop = nn.Dropout(p=dropout)
#         self.classifier = nn.Linear(self.backbone.config.hidden_size, n_classes)

#     def forward(self, input_ids, attention_mask):
#         out = self.backbone(input_ids=input_ids, attention_mask=attention_mask)
#         pooled = out.last_hidden_state[:, 0, :]
#         pooled = self.drop(pooled)
#         logits = self.classifier(pooled)
#         return logits

# # --- THRESHOLD UTILITIES ---
# def find_optimal_thresholds(y_true, y_probs, label_cols, num_thresholds=100):
#     optimal_thresholds = {}
#     for i, label in enumerate(label_cols):
#         best_f1, best_t = 0.0, 0.5
#         for t in np.linspace(0.0, 1.0, num_thresholds):
#             y_pred_l = (y_probs[:, i] > t).astype(int)
#             f1 = f1_score(y_true[:, i], y_pred_l, zero_division=0)
#             if f1 > best_f1:
#                 best_f1, best_t = f1, t
#         optimal_thresholds[label] = best_t
#         print(f" > Optimal threshold for {label}: {best_t:.4f} (Label F1: {best_f1:.4f})")
#     return optimal_thresholds

# def calculate_macro_f1(y_true, y_probs, optimal_thresholds, label_cols):
#     y_pred = np.zeros_like(y_true)
#     for i, label in enumerate(label_cols):
#         t = optimal_thresholds[label]
#         y_pred[:, i] = (y_probs[:, i] > t).astype(int)
#     return f1_score(y_true, y_pred, average='macro', zero_division=0)

In [11]:
# def train_model():
#     LABEL_COLS = label_cols
#     wandb.init(project="22f3001086-t32025", name = "Finetuned DeBERTa", config=CONFIG)
#     cfg = wandb.config

#     model = DebertaClassifier(
#         n_classes=cfg.OUTPUT_DIM,
#         model_name=cfg.MODEL_NAME,
#         dropout=cfg.DROPOUT
#     ).to(DEVICE)

#     loss_fn = nn.BCEWithLogitsLoss(pos_weight=POS_WEIGHTS).to(DEVICE)

#     optimizer = AdamW(
#         model.parameters(),
#         lr=cfg.LEARNING_RATE,
#         weight_decay=cfg.WEIGHT_DECAY
#     )

#     total_steps = len(train_loader) * cfg.EPOCHS
#     warmup_steps = int(total_steps * cfg.WARMUP_RATIO)
#     scheduler = get_linear_schedule_with_warmup(
#         optimizer,
#         num_warmup_steps=warmup_steps,
#         num_training_steps=total_steps
#     )

#     best_macro_f1 = -1.0

#     for epoch in range(cfg.EPOCHS):
#         # TRAIN
#         model.train()
#         total_loss = 0.0
#         for batch in tqdm(train_loader, desc=f"Epoch {epoch+1} Training", leave=False):
#             optimizer.zero_grad()
#             input_ids = batch['input_ids'].to(DEVICE)
#             attention_mask = batch['attention_mask'].to(DEVICE)
#             labels = batch['labels'].to(DEVICE)

#             logits = model(input_ids=input_ids, attention_mask=attention_mask)
#             loss = loss_fn(logits, labels)
#             total_loss += loss.item()

#             loss.backward()
#             nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
#             optimizer.step()
#             scheduler.step()

#         avg_train_loss = total_loss / len(train_loader)

#         # VALIDATION
#         model.eval()
#         all_labels, all_probs = [], []
#         with torch.no_grad():
#             for batch in tqdm(val_loader, desc="Validation", leave=False):
#                 input_ids = batch['input_ids'].to(DEVICE)
#                 attention_mask = batch['attention_mask'].to(DEVICE)
#                 labels = batch['labels'].cpu().numpy()

#                 logits = model(input_ids=input_ids, attention_mask=attention_mask)
#                 probs = torch.sigmoid(logits).cpu().numpy()

#                 all_labels.append(labels)
#                 all_probs.append(probs)

#         y_true = np.vstack(all_labels)
#         y_probs = np.vstack(all_probs)

#         print(f"\n--- Finding Optimal Thresholds for Epoch {epoch+1} ---")
#         optimal_thresholds = find_optimal_thresholds(y_true, y_probs, LABEL_COLS)
#         macro_f1_val = calculate_macro_f1(y_true, y_probs, optimal_thresholds, LABEL_COLS)

#         print(f"\n--- Epoch {epoch+1} Results ---")
#         print(f"Train Loss: {avg_train_loss:.4f}")
#         print(f"Validation Macro F1 (Optimal Thresholds): {macro_f1_val:.4f}")

#         wandb.log({
#             "epoch": epoch + 1,
#             "train_loss": avg_train_loss,
#             "val_macro_f1": macro_f1_val,
#             "learning_rate": optimizer.param_groups[0]["lr"],
#             **{f"T_{k}": v for k, v in optimal_thresholds.items()}
#         })

#         if macro_f1_val > best_macro_f1:
#             best_macro_f1 = macro_f1_val
#             print(f"New best model! Saving with Macro F1: {best_macro_f1:.4f}")
#             torch.save(model.state_dict(), f"best_deberta_{best_macro_f1:.4f}.pt")
#             np.save("optimal_thresholds_deberta.npy", optimal_thresholds)

#     wandb.finish()

# train_model()
# print("\nTraining complete.")

Epoch 1 Training:   0%|          | 0/253 [00:00<?, ?it/s]

Validation:   0%|          | 0/43 [00:00<?, ?it/s]


--- Finding Optimal Thresholds for Epoch 1 ---
 > Optimal threshold for anger: 0.9091 (Label F1: 0.7173)
 > Optimal threshold for fear: 0.5253 (Label F1: 0.8120)
 > Optimal threshold for joy: 0.8485 (Label F1: 0.7515)
 > Optimal threshold for sadness: 0.6667 (Label F1: 0.7670)
 > Optimal threshold for surprise: 0.7879 (Label F1: 0.7581)

--- Epoch 1 Results ---
Train Loss: 1.0864
Validation Macro F1 (Optimal Thresholds): 0.7612
New best model! Saving with Macro F1: 0.7612


Epoch 2 Training:   0%|          | 0/253 [00:00<?, ?it/s]

Validation:   0%|          | 0/43 [00:00<?, ?it/s]

...

Epoch 6 Training:   0%|          | 0/253 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7a23cd5d2de0>
Traceback (most recent call last):
Exception ignored in:   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1618, in __del__
<function _MultiProcessingDataLoaderIter.__del__ at 0x7a23cd5d2de0>
    Traceback (most recent call last):
self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1618, in __del__
      File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1601, in _shutdown_workers
self._shutdown_workers()
      File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1601, in _shutdown_workers
if w.is_alive():
     if w.is_alive():
           ^  ^^^^^^^^^^^^^^^^^^^^^^^

  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'  File "/usr/lib/python3

Validation:   0%|          | 0/43 [00:00<?, ?it/s]


--- Finding Optimal Thresholds for Epoch 6 ---
 > Optimal threshold for anger: 0.8586 (Label F1: 0.7987)
 > Optimal threshold for fear: 0.6162 (Label F1: 0.8850)
 > Optimal threshold for joy: 0.8687 (Label F1: 0.8754)
 > Optimal threshold for sadness: 0.7778 (Label F1: 0.8552)
 > Optimal threshold for surprise: 0.8283 (Label F1: 0.8646)

--- Epoch 6 Results ---
Train Loss: 0.1260
Validation Macro F1 (Optimal Thresholds): 0.8558
New best model! Saving with Macro F1: 0.8558



Training complete.


--- Finding Optimal Thresholds for Epoch 1 ---
 > Optimal threshold for anger: 0.9091 (Label F1: 0.7173)
 > Optimal threshold for fear: 0.5253 (Label F1: 0.8120)
 > Optimal threshold for joy: 0.8485 (Label F1: 0.7515)
 > Optimal threshold for sadness: 0.6667 (Label F1: 0.7670)
 > Optimal threshold for surprise: 0.7879 (Label F1: 0.7581)

--- Epoch 1 Results ---
Train Loss: 1.0864
Validation Macro F1 (Optimal Thresholds): 0.7612
New best model! Saving with Macro F1: 0.7612

--- Finding Optimal Thresholds for Epoch 2 ---
 > Optimal threshold for anger: 0.8788 (Label F1: 0.7601)
 > Optimal threshold for fear: 0.7677 (Label F1: 0.8465)
 > Optimal threshold for joy: 0.5051 (Label F1: 0.8051)
 > Optimal threshold for sadness: 0.8182 (Label F1: 0.8000)
 > Optimal threshold for surprise: 0.6566 (Label F1: 0.8177)

--- Epoch 2 Results ---
Train Loss: 0.5477
Validation Macro F1 (Optimal Thresholds): 0.8059
New best model! Saving with Macro F1: 0.8059

--- Finding Optimal Thresholds for Epoch 3 ---
 > Optimal threshold for anger: 0.6768 (Label F1: 0.7697)
 > Optimal threshold for fear: 0.6869 (Label F1: 0.8701)
 > Optimal threshold for joy: 0.9091 (Label F1: 0.8406)
 > Optimal threshold for sadness: 0.8788 (Label F1: 0.8331)
 > Optimal threshold for surprise: 0.5556 (Label F1: 0.8418)

--- Epoch 3 Results ---
Train Loss: 0.3380
Validation Macro F1 (Optimal Thresholds): 0.8311
New best model! Saving with Macro F1: 0.8311

--- Finding Optimal Thresholds for Epoch 4 ---
 > Optimal threshold for anger: 0.7475 (Label F1: 0.8091)
 > Optimal threshold for fear: 0.6768 (Label F1: 0.8797)
 > Optimal threshold for joy: 0.9091 (Label F1: 0.8540)
 > Optimal threshold for sadness: 0.6465 (Label F1: 0.8521)
 > Optimal threshold for surprise: 0.9091 (Label F1: 0.8533)

--- Epoch 4 Results ---
Train Loss: 0.2248
Validation Macro F1 (Optimal Thresholds): 0.8496
New best model! Saving with Macro F1: 0.8496

--- Finding Optimal Thresholds for Epoch 5 ---
 > Optimal threshold for anger: 0.5758 (Label F1: 0.7962)
 > Optimal threshold for fear: 0.6263 (Label F1: 0.8817)
 > Optimal threshold for joy: 0.9192 (Label F1: 0.8668)
 > Optimal threshold for sadness: 0.7980 (Label F1: 0.8548)
 > Optimal threshold for surprise: 0.7576 (Label F1: 0.8622)

--- Epoch 5 Results ---
Train Loss: 0.1617
Validation Macro F1 (Optimal Thresholds): 0.8523
New best model! Saving with Macro F1: 0.8523

--- Finding Optimal Thresholds for Epoch 6 ---
 > Optimal threshold for anger: 0.8586 (Label F1: 0.7987)
 > Optimal threshold for fear: 0.6162 (Label F1: 0.8850)
 > Optimal threshold for joy: 0.8687 (Label F1: 0.8754)
 > Optimal threshold for sadness: 0.7778 (Label F1: 0.8552)
 > Optimal threshold for surprise: 0.8283 (Label F1: 0.8646)

--- Epoch 6 Results ---
Train Loss: 0.1260
Validation Macro F1 (Optimal Thresholds): 0.8558
New best model! Saving with Macro F1: 0.8558

In [13]:
# import torch
# import pandas as pd
# import numpy as np
# from torch.utils.data import DataLoader
# from transformers import AutoTokenizer, AutoModel
# import torch.nn as nn
# from tqdm.auto import tqdm

# CONFIG_INF = {
#     'MODEL_NAME': 'microsoft/deberta-v3-base',
#     'MAX_LEN': 128,
#     'OUTPUT_DIM': 5
# }
# DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
# LABEL_COLS = ['anger','fear','joy','sadness','surprise']

# class DebertaClassifier(nn.Module):
#     def __init__(self, n_classes, model_name, dropout):
#         super(DebertaClassifier, self).__init__()
#         self.backbone = AutoModel.from_pretrained(model_name)
#         self.drop = nn.Dropout(p=dropout)
#         self.classifier = nn.Linear(self.backbone.config.hidden_size, n_classes)

#     def forward(self, input_ids, attention_mask):
#         out = self.backbone(input_ids=input_ids, attention_mask=attention_mask)
#         pooled = out.last_hidden_state[:, 0, :]
#         pooled = self.drop(pooled)
#         logits = self.classifier(pooled)
#         return logits

# class EmotionTestDataset(torch.utils.data.Dataset):
#     def __init__(self, df, tokenizer, max_len):
#         self.texts = df['text'].values
#         self.tokenizer = tokenizer
#         self.max_len = max_len

#     def __len__(self):
#         return len(self.texts)

#     def __getitem__(self, index):
#         text = str(self.texts[index])
#         enc = self.tokenizer.encode_plus(
#             text,
#             add_special_tokens=True,
#             max_length=self.max_len,
#             padding='max_length',
#             truncation=True,
#             return_attention_mask=True,
#             return_tensors='pt',
#         )
#         return {
#             'input_ids': enc['input_ids'].flatten(),
#             'attention_mask': enc['attention_mask'].flatten()
#         }

# def predict_test_probs(model_path, batch_size=64):
#     print(f"Loading tokenizer and model from {model_path}...")
#     tokenizer = AutoTokenizer.from_pretrained(CONFIG_INF['MODEL_NAME'])

#     model = DebertaClassifier(
#         n_classes=CONFIG_INF['OUTPUT_DIM'],
#         model_name=CONFIG_INF['MODEL_NAME'],
#         dropout=0.1
#     )
#     model.load_state_dict(torch.load(model_path, map_location=DEVICE))
#     model.to(DEVICE)
#     model.eval()

#     df_test = dt.copy()
#     test_ds = EmotionTestDataset(df_test, tokenizer, CONFIG_INF['MAX_LEN'])
#     test_loader = DataLoader(test_ds, batch_size=batch_size, shuffle=False, num_workers=2)

#     all_probs = []
#     with torch.no_grad():
#         for batch in tqdm(test_loader, desc='Generating Test Predictions', leave=False):
#             input_ids = batch['input_ids'].to(DEVICE)
#             attention_mask = batch['attention_mask'].to(DEVICE)
#             logits = model(input_ids=input_ids, attention_mask=attention_mask)
#             probs = torch.sigmoid(logits).cpu().numpy()
#             all_probs.append(probs)

#     test_probs = np.vstack(all_probs)
#     np.save("deberta_test_probs.npy", test_probs)
#     print(f"\nPredictions saved to deberta_test_probs.npy. Shape: {test_probs.shape}")
#     return test_probs, df_test

# # use the best checkpoint name printed during training
# BEST_MODEL_PATH = "/kaggle/working/best_deberta_0.8558.pt" 
# deberta_test_probs, df_test = predict_test_probs(BEST_MODEL_PATH)

# try:
#     optimal_thresholds = np.load("/kaggle/working/optimal_thresholds_deberta.npy", allow_pickle=True).item()
#     print("\nLoaded optimal thresholds:", optimal_thresholds)
# except FileNotFoundError:
#     print("\nWARNING: thresholds file not found, using 0.5.")
#     optimal_thresholds = {k: 0.5 for k in LABEL_COLS}

# df_submission = df_test[['id']].copy()
# for i, label in enumerate(LABEL_COLS):
#     thr = optimal_thresholds.get(label, 0.5)
#     df_submission[label] = (deberta_test_probs[:, i] > thr).astype(int)

# df_submission.to_csv("submission_deberta.csv", index=False)
# df_submission.head()

Loading tokenizer and model from /kaggle/working/best_deberta_0.8558.pt...


Generating Test Predictions:   0%|          | 0/27 [00:00<?, ?it/s]


Predictions saved to deberta_test_probs.npy. Shape: (1707, 5)

Loaded optimal thresholds: {'anger': 0.8585858585858587, 'fear': 0.6161616161616162, 'joy': 0.8686868686868687, 'sadness': 0.7777777777777778, 'surprise': 0.8282828282828284}


id  anger  fear  joy  sadness  surprise
0   0      1     1    0        1         0
1   1      0     0    0        0         0
2   2      1     1    0        0         0
3   3      0     1    0        0         0
4   4      0     1    0        0         1

In [ ]:
# # --- DEBERTA INFERENCE: SELF-CONTAINED BLOCK ---

# import numpy as np
# import pandas as pd
# import torch
# import torch.nn as nn
# from torch.utils.data import DataLoader, Dataset
# from transformers import AutoTokenizer, AutoModel
# from tqdm.auto import tqdm

# # Paths you MUST set correctly:
# BEST_MODEL_PATH = "/kaggle/input/sub-files-dlgenai/best_deberta_0.8594.pt"      # update
# THRESH_PATH     = "/kaggle/input/sub-files-dlgenai/optimal_thresholds_deberta.npy"  # update
# TEST_PATH       = "/kaggle/input/2025-sep-dl-gen-ai-project/test.csv"           # competition test

# LABEL_COLS = ['anger','fear','joy','sadness','surprise']

# CONFIG_INF = {
#     'MODEL_NAME': 'microsoft/deberta-v3-base',
#     'MAX_LEN': 128,
#     'OUTPUT_DIM': len(LABEL_COLS),
# }
# DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# print("Using device:", DEVICE)

# # ---- Model definition ----
# class DebertaClassifier(nn.Module):
#     def __init__(self, n_classes, model_name, dropout):
#         super(DebertaClassifier, self).__init__()
#         self.backbone = AutoModel.from_pretrained(model_name)
#         self.drop = nn.Dropout(p=dropout)
#         self.classifier = nn.Linear(self.backbone.config.hidden_size, n_classes)

#     def forward(self, input_ids, attention_mask):
#         out = self.backbone(input_ids=input_ids, attention_mask=attention_mask)
#         pooled = out.last_hidden_state[:, 0, :]
#         pooled = self.drop(pooled)
#         logits = self.classifier(pooled)
#         return logits

# # ---- Dataset for test ----
# class EmotionTestDataset(Dataset):
#     def __init__(self, texts, tokenizer, max_len):
#         self.texts = list(texts)
#         self.tokenizer = tokenizer
#         self.max_len = max_len

#     def __len__(self):
#         return len(self.texts)

#     def __getitem__(self, index):
#         text = str(self.texts[index])
#         enc = self.tokenizer.encode_plus(
#             text,
#             add_special_tokens=True,
#             max_length=self.max_len,
#             padding="max_length",
#             truncation=True,
#             return_attention_mask=True,
#             return_tensors="pt",
#         )
#         return {
#             "input_ids": enc["input_ids"].squeeze(0),
#             "attention_mask": enc["attention_mask"].squeeze(0),
#         }

# # ---- Prediction helper ----
# def predict_test_probs(model_path, test_path, batch_size=64):
#     print(f"Loading test data from {test_path}")
#     df_test = pd.read_csv(test_path)

#     tokenizer = AutoTokenizer.from_pretrained(CONFIG_INF["MODEL_NAME"])

#     model = DebertaClassifier(
#         n_classes=CONFIG_INF["OUTPUT_DIM"],
#         model_name=CONFIG_INF["MODEL_NAME"],
#         dropout=0.1
#     )
#     model.load_state_dict(torch.load(model_path, map_location=DEVICE))
#     model.to(DEVICE)
#     model.eval()

#     test_ds = EmotionTestDataset(df_test["text"], tokenizer, CONFIG_INF["MAX_LEN"])
#     test_loader = DataLoader(test_ds, batch_size=batch_size, shuffle=False, num_workers=2)

#     all_probs = []
#     with torch.no_grad():
#         for batch in tqdm(test_loader, desc="DeBERTa Test Predictions", leave=False):
#             input_ids = batch["input_ids"].to(DEVICE)
#             attention_mask = batch["attention_mask"].to(DEVICE)
#             logits = model(input_ids=input_ids, attention_mask=attention_mask)
#             probs = torch.sigmoid(logits).cpu().numpy()
#             all_probs.append(probs)

#     test_probs = np.vstack(all_probs)
#     print("Probabilities shape:", test_probs.shape)
#     return test_probs, df_test

# # ---- Run inference ----
# deberta_test_probs, df_test = predict_test_probs(BEST_MODEL_PATH, TEST_PATH)

# # Load label-wise optimal thresholds
# try:
#     optimal_thresholds = np.load(THRESH_PATH, allow_pickle=True).item()
#     print("Loaded optimal thresholds:", optimal_thresholds)
# except FileNotFoundError:
#     print("WARNING: thresholds file not found, using 0.5 for all labels.")
#     optimal_thresholds = {k: 0.5 for k in LABEL_COLS}

# # Build submission
# df_submission = df_test[["id"]].copy()
# for i, label in enumerate(LABEL_COLS):
#     thr = optimal_thresholds.get(label, 0.5)
#     df_submission[label] = (deberta_test_probs[:, i] > thr).astype(int)

# df_submission.to_csv("submission_deberta.csv", index=False)
# df_submission.head()